In [1]:
import getpass

secret_key = getpass.getpass("enter key:")

enter key:········


In [1]:
!pip install openai

In [2]:
!pip install --upgrade openai
!pip install python-docx


In [1]:
import os
import openai
import docx  # Library to handle Word documents
import csv
import unicodedata



In [2]:
from openai import OpenAI
client = OpenAI()

completion = client.chat.completions.create(
  model="o1-mini-2024-09-12",
  messages=[
    {"role": "user", 
     "content": "Hello!"}
  ]
)

print(completion.choices[0].message)


ChatCompletionMessage(content='Hello! How can I assist you today?', refusal=None, role='assistant', audio=None, function_call=None, tool_calls=None)


In [4]:
# Function to extract text from .txt files
def extract_text_from_txt(txt_path):
    try:
        with open(txt_path, "r", encoding="utf-8") as file:
            text = file.read()
        return text
    except Exception as e:
        return f"Error processing file {txt_path}: {e}"

In [5]:
# Function to process text files and extract data using OpenAI API
def process_txt_files(txt_paths, individual_folder):
    combined_data = []
    
    # Ensure the folder for individual CSVs exists
    os.makedirs(individual_folder, exist_ok=True)

    for txt_path in txt_paths:
        text = extract_text_from_txt(txt_path)
        if text.startswith("Error"):
            print(text)  # Print error message if any
            continue

        # Prepare messages for OpenAI chat completion
        messages = [
            {"role": "user", "content": "a multicolumn spreadsheet from the given text | article doi| product | product concentration | Carbon source | Carbon source concentration | yield | media | time | mode of bioreactor operation | strain name | parent strain | knocked out genes | overexpressed native genes | heterologous genes| Promotor | genome integration Y/N | codon optimized | culture volume | culture vessel: Shake flask, Batch, fedbatch, chemostat, microplates | nitrogen condition: sufficient, limited |oxygen condition: sufficient, limited, anaerobic | pH | temperature | Direct evolution Y/N | When outputting the daughter strain, you need to include the expressed and knockout genes in the parent strain. always provide full table, if data not provided, just leave as NA, Do not provide explanations and notes"},
            {"role": "user", "content": text}
        ]

        # Get completion from OpenAI
        try:
            completion = client.chat.completions.create(
                model="o1-mini-2024-09-12",
                messages=messages
            )

            # Extract data
            extracted_data = completion.choices[0].message.content
            print(f"Data extracted from {txt_path}: {extracted_data}")

            # Normalize and split data into rows
            normalized_data = unicodedata.normalize('NFKD', extracted_data)
            lines = normalized_data.strip().split("\n")
            rows = [line.strip().split("|") for line in lines if line.strip()]

            # Clean up spaces in each cell
            rows = [[cell.strip() for cell in row] for row in rows]

            # Save each extracted data as an individual CSV file
            csv_file_name = os.path.basename(txt_path).replace('.txt', '.csv')
            individual_csv_path = os.path.join(individual_folder, csv_file_name)
            with open(individual_csv_path, mode='w', newline='', encoding='utf-8-sig') as file:
                writer = csv.writer(file)
                writer.writerows(rows)

            # Add rows to combined data (skip header rows for now)
            combined_data.extend(rows[1:] if len(rows) > 1 else [])
        except Exception as e:
            print(f"Failed to process file {txt_path}: {e}")

    return combined_data




In [9]:
# Function to get all .txt file paths in a folder
def get_txt_paths(folder_path):
    return [os.path.join(folder_path, f) for f in os.listdir(folder_path) if f.endswith('.txt')]

In [11]:
# Function to save the combined data into a single CSV file
def save_combined_csv(data, output_csv_path, headers):
    # Ensure the directory for the combined CSV file exists
    os.makedirs(os.path.dirname(output_csv_path), exist_ok=True)

    # Write the combined data to a CSV file
    with open(output_csv_path, mode='w', newline='', encoding='utf-8-sig') as file:
        writer = csv.writer(file)
        writer.writerow(headers)
        writer.writerows(data)
    
    print(f"Combined data saved to {output_csv_path}")


In [13]:
# Main execution
folder_path = r'E:\Paper\Yarrowia\Yarrowia Biotech PDFs\txt_word'
individual_folder = r'E:\Paper\Yarrowia\Yarrowia Biotech PDFs\individual_csvs_20241126'
output_csv_path = r'E:\Paper\Yarrowia\Yarrowia Biotech PDFs\Yarrowia_combined_20241126.csv'
# Get all text file paths
txt_paths = get_txt_paths(folder_path)

# Process all text files and save individual CSVs
combined_data = process_txt_files(txt_paths, individual_folder)

# Define headers based on the structured format
headers = [
    "article doi", "product", "product concentration", "carbon source", "carbon source concentration",  "yield", 
    "media", "time", "mode of bioreactor operation", "strain name", "parent strain", 
    "knocked out genes", "overexpressed native genes", "heterologous genes", "Promotor", 
    "genome integration Y/N", "codon optimized", "culture volume", "culture vessel", 
    "nitrogen condition", "oxygen condition", "pH", "temperature", 
    "Direct evolution Y/N"
]

# Save the combined data into a single CSV file
save_combined_csv(combined_data, output_csv_path, headers)

Data extracted from E:\Paper\Yarrowia\Yarrowia Biotech PDFs\txt_word\Yarrowia_0001.txt: | article doi | product        | product concentration | Carbon source | Carbon source concentration      | yield          | media                                         | time                | mode of bioreactor operation | strain name             | parent strain            | knocked out genes | overexpressed native genes | heterologous genes | Promotor     | genome integration Y/N | codon optimized | culture volume | culture vessel    | nitrogen condition | oxygen condition              | pH   | temperature | Direct evolution Y/N |
|-------------|----------------|-----------------------|---------------|----------------------------------|----------------|-----------------------------------------------|---------------------|------------------------------|-------------------------|--------------------------|-------------------|----------------------------|--------------------|--------------|--------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0081.docx: | article doi           | product     | product concentration | substrate     | substrate concentration | media                                       | time | mode of bioreactor operation | strain name       | parent strain | knocked out genes | overexpressed native genes | heterologous genes | Promotor | Parent strain | genome integration Y/N | codon optimized | culture volume | culture vessel | nitrogen condition | oxygen condition | time | pH | temperature | Direct evolution Y/N |
|-----------------------|-------------|-----------------------|---------------|-------------------------|---------------------------------------------|------|------------------------------|-------------------|---------------|-------------------|----------------------------|--------------------|----------|---------------|------------------------|-----------------|----------------|-----------------|---------------------|-------------------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0085.docx: | article doi                             | product | product concentration | substrate | substrate concentration | media               | time | mode of bioreactor operation | strain name               | parent strain       | knocked out genes | overexpressed native genes | heterologous genes       | Promotor                                | Parent strain       | genome integration Y/N | codon optimized | culture volume | culture vessel: Shake flask, Batch, fedbatch, chemostat, microplates | media               | nitrogen condition: sufficient, limited | oxygen condition: sufficient, limited, anaerobic | time | pH  | temperature | Direct evolution Y/N |
|-----------------------------------------|---------|-----------------------|-----------|-------------------------|---------------------|------|------------------------------|---------------------------|---------------------|-------------------|-----------------------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0089.docx: | article doi            | product | product concentration | substrate | substrate concentration | media                             | time | mode of bioreactor operation | strain name                 | parent strain   | knocked out genes | overexpressed native genes | heterologous genes | Promotor | Parent strain   | genome integration Y/N | codon optimized | culture volume | culture vessel | media                             | nitrogen condition | oxygen condition | time | pH     | temperature | Direct evolution Y/N |
|------------------------|---------|-----------------------|-----------|-------------------------|-----------------------------------|------|------------------------------|-----------------------------|------------------|-------------------|----------------------------|--------------------|----------|------------------|------------------------|-----------------|----------------|----------------|------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0093.docx: | article doi                     | product      | product concentration | substrate              | substrate concentration                   | media | time | mode of bioreactor operation | strain name  | parent strain | knocked out genes | overexpressed native genes | heterologous genes | Promotor | Parent strain | genome integration Y/N | codon optimized | culture volume | culture vessel                 | media | nitrogen condition | oxygen condition          | time | pH  | temperature | Direct evolution Y/N |
|---------------------------------|--------------|-----------------------|------------------------|--------------------------------------------|-------|------|------------------------------|--------------|---------------|-------------------|----------------------------|--------------------|----------|---------------|------------------------|-----------------|----------------|--------------------------------|-

...

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0373.docx: | article doi                     | product        | product concentration | substrate   | substrate concentration | media   | time | mode of bioreactor operation | strain name | parent strain    | knocked out genes | overexpressed native genes | heterologous genes | Promotor | Parent strain    | genome integration Y/N | codon optimized | culture volume | culture vessel | media   | nitrogen condition | oxygen condition | time | pH   | temperature | Direct evolution Y/N |
|---------------------------------|----------------|-----------------------|-------------|-------------------------|---------|------|------------------------------|-------------|-------------------|-------------------|---------------------------|--------------------|----------|-------------------|------------------------|-----------------|----------------|----------------|---------|---------------------|-------------------|------|------|-------------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0378.docx: | article doi                 | product                   | product concentration | substrate | substrate concentration | media                                                                       | time | mode of bioreactor operation | strain name                     | parent strain | knocked out genes                             | overexpressed native genes | heterologous genes                       | Promotor | genome integration Y/N | codon optimized | culture volume | culture vessel | nitrogen condition | oxygen condition | time  | pH  | temperature | Direct evolution Y/N |
|-----------------------------|---------------------------|------------------------|-----------|-------------------------|-----------------------------------------------------------------------------|------|------------------------------|---------------------------------|---------------|------------------------------------------------|------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0382.docx: | article doi               | product                   | product concentration | substrate | substrate concentration | media  | time | mode of bioreactor operation | strain name                | parent strain | knocked out genes           | overexpressed native genes | heterologous genes          | Promotor | Parent strain | genome integration Y/N | codon optimized | culture volume | culture vessel                          | media    | nitrogen condition | oxygen condition | time      | pH | temperature | Direct evolution Y/N |
|---------------------------|---------------------------|-----------------------|-----------|-------------------------|--------|------|------------------------------|----------------------------|---------------|-----------------------------|----------------------------|-----------------------------|----------|---------------|------------------------|------------------|----------------|-------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0387.docx: | article doi        | product     | product concentration          | substrate   | substrate concentration | media | time          | mode of bioreactor operation | strain name | parent strain       | knocked out genes | overexpressed native genes | heterologous genes           | Promotor | Parent strain | genome integration Y/N | codon optimized | culture volume | culture vessel | media | nitrogen condition | oxygen condition | time          | pH | temperature | Direct evolution Y/N |
|--------------------|-------------|--------------------------------|-------------|-------------------------|-------|---------------|------------------------------|-------------|---------------------|-------------------|----------------------------|------------------------------|----------|---------------|------------------------|-----------------|----------------|----------------|-------|--------------------|-------------------|------

Data extracted from E:\Paper\EColi_database\Word_Doc\EColi_0390.docx: | article doi        | product            | product concentration | substrate            | substrate concentration                            | media             | time (h) | mode of bioreactor operation | strain name                         | parent strain           | knocked out genes | overexpressed native genes | heterologous genes                                                               | Promotor | genome integration Y/N | codon optimized | culture volume | culture vessel | nitrogen condition | oxygen condition | pH   | temperature | Direct evolution Y/N |
|--------------------|--------------------|-----------------------|----------------------|-----------------------------------------------------|-------------------|----------|-----------------------------|-------------------------------------|-------------------------|-------------------|----------------------------|--------------------------------------

In [37]:
import pandas as pd
import re

# Load the CSV file with specified encoding
file_path = r'E:\Paper\Saccharomyces database\Sorted Saccharomyces PDFs\Saccharomyces_combined_20241121.csv'  # Replace with your file path
data = pd.read_csv(file_path, encoding='utf-8-sig')  # Adjust encoding if necessary

# Separate the header rows from the data rows
header = data.iloc[:2]  # Keep rows 0 and 1 as header rows
data_rows = data.iloc[2:]  # Start cleaning from row 2 onwards

# Define a regex pattern to match unwanted values in 'article doi' column
unwanted_article_doi_pattern = r'^(NA|article doi|Article DOI|article_doi|[-]+|\s*|[.]+)$'

# Function to standardize DOIs to start with '10.'
def standardize_doi(doi):
    if isinstance(doi, str):
        # Remove any leading 'http://dx.doi.org/' or 'https://doi.org/' prefixes
        doi = re.sub(r'^(https?://(dx\.)?doi\.org/)', '', doi, flags=re.IGNORECASE)
        # Ensure DOI starts with '10.'
        if not doi.startswith("10."):
            return None  # Return None for non-standard DOIs
    return doi

# Apply the function to the 'article doi' column
data_rows['article doi'] = data_rows['article doi'].apply(standardize_doi)

# Filter out rows where 'article doi' column has unwanted values or 'product concentration' is empty
filtered_data_rows = data_rows[
    ~data_rows['article doi'].fillna('').str.match(unwanted_article_doi_pattern, na=False) &
    data_rows['product concentration'].notna() & (data_rows['product concentration'] != '')
]

# Combine the header with the filtered data rows
final_data = pd.concat([header, filtered_data_rows], ignore_index=True)

# Export the cleaned data to a new CSV file with encoding specified
cleaned_file_path = r'E:\Paper\Saccharomyces database\Sorted Saccharomyces PDFs\Cleaned_Saccharomyces_combined_20241121.csv'  # Adjust the path and file name as needed
final_data.to_csv(cleaned_file_path, index=False, encoding='utf-8-sig')

print(f"Cleaned data has been saved to {cleaned_file_path}")


ParserError: Error tokenizing data. C error: Expected 26 fields in line 940, saw 27


In [29]:
import pandas as pd
import re

# Load the CSV file with specified encoding
file_path = r'E:\Paper\Ecoli_database\Ecoli_combined_20241120.csv'  # Replace with your file path
data = pd.read_csv(file_path, encoding='utf-8-sig')  # Adjust encoding if necessary

# Separate the header rows from the data rows
header = data.iloc[:2]  # Keep rows 0 and 1 as header rows
data_rows = data.iloc[2:].copy()  # Start cleaning from row 2 (explicit copy to avoid warning)

# Define a regex pattern to match unwanted values in 'article doi' column
unwanted_article_doi_pattern = r'^(NA|article doi|Article DOI|article_doi[-]+|\s*|.+)$'

# Function to standardize DOIs
def standardize_doi(doi):
    if isinstance(doi, str):
        # Remove any leading 'http://dx.doi.org/' or 'https://doi.org/' prefixes
        doi = re.sub(r'^(https?://(dx\.)?doi\.org/)', '', doi, flags=re.IGNORECASE)
        # Ensure DOI starts with '10.'
        if not doi.startswith("10."):
            return None  # Return None for non-standard DOIs
        return doi.strip()
    return None

# Apply the function to the 'article doi' column
data_rows['article doi'] = data_rows['article doi'].apply(standardize_doi)

# Filter out rows where 'article doi' column has unwanted values or 'product concentration' is empty
filtered_data_rows = data_rows[
    data_rows['article doi'].fillna('').str.match(unwanted_article_doi_pattern, na=False) &
    data_rows['product concentration'].notna() & (data_rows['product concentration'] != '')
].copy()  # Use copy() here to avoid warnings

# Combine the header with the filtered data rows
final_data = pd.concat([header, filtered_data_rows], ignore_index=True)

# Export the cleaned data to a new CSV file with encoding specified
cleaned_file_path = r'E:\Paper\Ecoli_database\Cleaned_EColi_combined_20241120.csv'  # Adjust the path and file name as needed
final_data.to_csv(cleaned_file_path, index=False, encoding='utf-8-sig')

print(f"Cleaned data has been saved to {cleaned_file_path}")

Cleaned data has been saved to E:\Paper\Ecoli_database\Cleaned_EColi_combined_20241120.csv
